In [ ]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    # Reshape X to 4-D tensor: [batch_size, width, height, channels]
    # MNIST images are 28x28 pixels, and have one color channel
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    # Computes 32 features using a 5x5 filter with ReLU activation.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 28, 28, 1]
    # Output Tensor Shape: [batch_size, 28, 28, 32]
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #1
    # First max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 28, 28, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 32]
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2
    # Computes 64 features using a 5x5 filter.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 14, 14, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 64]
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #2
    # Second max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 14, 14, 64]
    # Output Tensor Shape: [batch_size, 7, 7, 64]
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Flatten tensor into a batch of vectors
    # Input Tensor Shape: [batch_size, 7, 7, 64]
    # Output Tensor Shape: [batch_size, 7 * 7 * 64]
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

    # Dense Layer
    # Densely connected layer with 1024 neurons
    # Input Tensor Shape: [batch_size, 7 * 7 * 64]
    # Output Tensor Shape: [batch_size, 1024]
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

    # Add dropout operation; 0.6 probability that element will be kept
    dropout = tf.layers.dropout(
        inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits layer
    # Input Tensor Shape: [batch_size, 1024]
    # Output Tensor Shape: [batch_size, 10]
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1),
        # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
        # `logging_hook`.
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images  # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images  # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
        model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

    # Set up logging for predictions
    # Log the values in the "Softmax" tensor with label "probabilities"
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
        tensors=tensors_to_log, every_n_iter=50)

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)


if __name__ == "__main__":
    tf.app.run()

/usr/local/lib/python3.5/dist-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_tf_random_seed': None, '_global_id_in_cluster': 0, '_save_checkpoints_steps': None, '_task_id': 0, '_log_step_count_steps': 100, '_keep_checkpoint_max': 5, '_session_config': None, '_num_worker_replicas': 1, '_evaluation_master': '', '_save_checkpoints_secs': 600, '_task_type': 'worker', '_is_chief': True, '_model_dir': '/tmp/mnist_convnet_model', '_save_summary_steps': 100, '_num_ps_replicas': 0, '_master': '', '_service': None, '_cluster_spec': <tensorflow.python.training

INFO:tensorflow:loss = 2.3168714, step = 1
INFO:tensorflow:probabilities = [[0.09973533 0.09761813 0.09605437 0.10916958 0.09135495 0.11822049
  0.09716424 0.10498839 0.10047232 0.08522225]
 [0.11196458 0.08945014 0.10422717 0.09340823 0.09986251 0.10226614
  0.10178816 0.10573886 0.09588041 0.09541378]
 [0.10162744 0.09849749 0.1127886  0.10363497 0.09465598 0.11653376
  0.08666939 0.08435677 0.10783551 0.09340013]
 [0.09401287 0.09682448 0.10023515 0.10254586 0.10631163 0.11034878
  0.08658548 0.10897085 0.09931566 0.09484927]
 [0.08697132 0.1099738  0.09471477 0.12093999 0.0963321  0.09862138
  0.092834   0.09744475 0.10864962 0.09351826]
 [0.10353657 0.10997137 0.12341139 0.10951417 0.07813237 0.09348686
  0.0852346  0.08881976 0.11024399 0.09764889]
 [0.08991977 0.10595158 0.10860348 0.10435395 0.08121011 0.10790155
  0.09315584 0.10516007 0.10287084 0.10087284]
 [0.09635808 0.09634301 0.09788107 0.10291284 0.09688953 0.09612459
  0.09723499 0.10114959 0.10187732 0.11322901]
 [0.1

INFO:tensorflow:global_step/sec: 172.11
INFO:tensorflow:probabilities = [[0.099181   0.10501222 0.1021493  0.10613456 0.09100886 0.09665862
  0.10179311 0.10291442 0.09747964 0.09766831]
 [0.09223388 0.09590576 0.10036847 0.10518774 0.08978245 0.09245586
  0.10281456 0.10922899 0.10583586 0.1061864 ]
 [0.09005264 0.09898009 0.09702707 0.1041309  0.09686445 0.10638178
  0.10003027 0.10429713 0.10175864 0.10047702]
 [0.0893997  0.10910013 0.1057554  0.10209507 0.09264925 0.11005706
  0.08528645 0.11197184 0.10158549 0.09209954]
 [0.1071251  0.09932833 0.10406905 0.10160004 0.0960436  0.10012581
  0.10330959 0.09403692 0.09737001 0.09699155]
 [0.09837631 0.09626289 0.11122974 0.10637926 0.08912987 0.10039428
  0.09349664 0.09831654 0.10772612 0.09868835]
 [0.08499852 0.10316436 0.09615923 0.1089245  0.09966511 0.10255688
  0.09860054 0.09842148 0.10537655 0.10213281]
 [0.09402015 0.09651273 0.10110829 0.1061316  0.10775328 0.09554683
  0.09418088 0.10455446 0.09333801 0.10685384]
 [0.0937

INFO:tensorflow:loss = 2.2971933, step = 101 (0.588 sec)
INFO:tensorflow:probabilities = [[0.10133085 0.09504381 0.10620959 0.10517136 0.09050664 0.10394433
  0.10145093 0.10937259 0.09897934 0.0879906 ]
 [0.09746817 0.09293412 0.09884857 0.11140019 0.08719932 0.09826
  0.1019234  0.10390531 0.09221859 0.1158423 ]
 [0.09420871 0.09842584 0.09823593 0.1151178  0.09764422 0.09742342
  0.10272161 0.09338548 0.09873484 0.10410218]
 [0.09388239 0.10013361 0.10621604 0.10696679 0.08512254 0.09418991
  0.09899615 0.11208791 0.10434055 0.09806411]
 [0.10143706 0.09329261 0.10438946 0.10312224 0.09743622 0.09166099
  0.09728327 0.10995943 0.10362197 0.09779675]
 [0.10873222 0.09048895 0.10674909 0.10688429 0.08823819 0.10075906
  0.09163909 0.09424341 0.11316407 0.09910166]
 [0.09433353 0.08834694 0.10582928 0.11206122 0.10274677 0.09907845
  0.10334477 0.10703183 0.0939869  0.09324029]
 [0.10618396 0.11442678 0.10398909 0.10088526 0.08140067 0.09845834
  0.09204724 0.09126542 0.11496948 0.0963

...

INFO:tensorflow:loss = 0.1305688, step = 16901 (0.501 sec)
INFO:tensorflow:probabilities = [[0.00021219 0.00455741 0.00408402 0.00817542 0.00032527 0.00090099
  0.00264222 0.00011417 0.97804147 0.00094682]
 [0.00009795 0.00632289 0.00103672 0.01797566 0.00622332 0.00885736
  0.00008203 0.00100965 0.9196388  0.03875558]
 [0.00000403 0.00017251 0.0008728  0.00121267 0.00007398 0.00007384
  0.00000035 0.9818658  0.00009338 0.01563051]
 [0.0001506  0.00171067 0.00034862 0.00078109 0.00009907 0.00035279
  0.00007601 0.00016082 0.9960006  0.00031972]
 [0.00000128 0.         0.0000005  0.00001844 0.00000002 0.0000075
  0.         0.9998516  0.0000001  0.00012057]
 [0.00008703 0.99093235 0.00057803 0.00010083 0.00027275 0.0003084
  0.00403713 0.00049289 0.00301947 0.00017108]
 [0.00004052 0.00003133 0.0016458  0.98781383 0.00006412 0.00072892
  0.00007124 0.00000164 0.00954306 0.00005962]
 [0.00001576 0.00000017 0.00000778 0.00001078 0.003677   0.00000185
  0.00000065 0.00003683 0.00050151 0.9

INFO:tensorflow:global_step/sec: 199.995
INFO:tensorflow:probabilities = [[0.00000052 0.00001814 0.00017278 0.8848496  0.00005574 0.00351486
  0.00000012 0.01437393 0.01365497 0.08335926]
 [0.00001099 0.00000439 0.0251231  0.18342564 0.00000027 0.00302639
  0.00000131 0.00000117 0.7883056  0.00010109]
 [0.00080096 0.00073435 0.00477152 0.05397241 0.0009737  0.8625821
  0.00167859 0.00021302 0.06957188 0.00470157]
 [0.         0.00000011 0.00000362 0.00000747 0.9996716  0.00000201
  0.00000032 0.00000069 0.00000951 0.00030474]
 [0.00003107 0.00003646 0.00023602 0.00000178 0.00055261 0.00012435
  0.9989588  0.00000017 0.0000566  0.00000208]
 [0.00016612 0.0000062  0.94972634 0.00916176 0.00042398 0.00603378
  0.0339445  0.00000014 0.00053535 0.0000019 ]
 [0.00000053 0.00029321 0.00014586 0.00096746 0.87051487 0.00033817
  0.00006809 0.00016318 0.00051367 0.12699486]
 [0.00000091 0.00000008 0.00000095 0.00002216 0.00372489 0.00000213
  0.00000005 0.00012051 0.00003005 0.9960983 ]
 [0.0000

INFO:tensorflow:loss = 0.22247359, step = 17001 (0.497 sec)
INFO:tensorflow:probabilities = [[0.00012949 0.9899886  0.00040837 0.00008532 0.00034906 0.000229
  0.00176208 0.00063007 0.0063539  0.0000642 ]
 [0.00002832 0.00003844 0.00105724 0.00128382 0.00115645 0.00086635
  0.00028997 0.00012476 0.97992295 0.01523172]
 [0.00061109 0.00075675 0.00003479 0.00028775 0.0000091  0.9955754
  0.00058048 0.00009684 0.00204535 0.00000237]
 [0.00000174 0.00000018 0.00003276 0.9796537  0.00000082 0.00648693
  0.00000006 0.0000071  0.00241868 0.01139801]
 [0.00157721 0.000012   0.00012638 0.00070874 0.0003186  0.00029246
  0.00029373 0.00000235 0.99392927 0.00273929]
 [0.99993837 0.00000001 0.00004117 0.00000007 0.00000003 0.00001423
  0.00000117 0.00000007 0.00000256 0.00000227]
 [0.9957449  0.00000019 0.0001668  0.00000162 0.00000208 0.00041091
  0.00366659 0.00000018 0.00000537 0.00000125]
 [0.92851365 0.00036984 0.00266917 0.00127449 0.00013187 0.0020426
  0.03321851 0.00022324 0.03113464 0.00

INFO:tensorflow:global_step/sec: 201.51
INFO:tensorflow:probabilities = [[0.00001444 0.99843675 0.00045026 0.00002179 0.00001084 0.00000984
  0.00013422 0.00021505 0.00069157 0.0000153 ]
 [0.00000247 0.00009394 0.96113515 0.03858597 0.00000038 0.00001842
  0.00000654 0.00000018 0.00015685 0.00000017]
 [0.99983525 0.0000001  0.00010671 0.00000283 0.00000029 0.00000927
  0.00003952 0.0000004  0.00000486 0.00000077]
 [0.99585235 0.00000213 0.00049095 0.00013132 0.00000902 0.00144672
  0.00000512 0.00049946 0.00000547 0.00155746]
 [0.00002056 0.00015571 0.00043164 0.00039068 0.9668133  0.00041647
  0.00033636 0.00263703 0.00009946 0.02869876]
 [0.00028163 0.98484945 0.00429845 0.00036192 0.00006507 0.00237508
  0.00362525 0.00073283 0.00333789 0.00007246]
 [0.00000028 0.00037856 0.9986242  0.00019675 0.00000003 0.00000043
  0.00000004 0.00012181 0.00067796 0.00000003]
 [0.00096637 0.0000007  0.00000604 0.00020055 0.0002742  0.00000572
  0.00000059 0.6001245  0.00198117 0.3964402 ]
 [0.0000

INFO:tensorflow:loss = 0.15708852, step = 17101 (0.499 sec)
INFO:tensorflow:probabilities = [[0.00008743 0.00000625 0.0001806  0.00000321 0.00066085 0.00088539
  0.9981761  0.00000001 0.0000002  0.00000001]
 [0.999936   0.00000027 0.00002715 0.00000437 0.00000033 0.00000917
  0.00000519 0.00000034 0.00000147 0.00001585]
 [0.35547674 0.00218175 0.08859865 0.0228925  0.01294186 0.01710642
  0.1472467  0.00187305 0.34089935 0.01078298]
 [0.00004555 0.         0.00002183 0.00099346 0.00000016 0.9986656
  0.0000042  0.0000001  0.00025823 0.00001099]
 [0.00321032 0.00529461 0.00676979 0.00112404 0.41832784 0.09847928
  0.4656717  0.00031427 0.00075305 0.00005515]
 [0.2890588  0.0008822  0.00378929 0.00167514 0.00954191 0.02719667
  0.00060843 0.5026852  0.0354199  0.12914246]
 [0.00055299 0.00000416 0.00004122 0.00002303 0.00000194 0.9986689
  0.00067535 0.00000103 0.00003119 0.00000018]
 [0.00000632 0.00000144 0.00005826 0.00079563 0.00179024 0.00021468
  0.00000266 0.00071326 0.00201725 0.